In [ ]:
import datetime
from pandas.tseries.offsets import BDay, MonthEnd
import globeop_reports as go
import pandas as pd
import analytics
import numpy as np

from analytics.index_data import get_index_quotes
from analytics.scenarios import run_portfolio_scenarios
from analytics import BlackSwaption, CreditIndex, BlackSwaptionVolSurface, Portfolio,DualCorrTranche

from utils.db import dbconn, dbengine

from risk.tranches import get_tranche_portfolio
from risk.swaptions import get_swaption_portfolio
from risk.bonds import subprime_risk, clo_risk, crt_risk

dawn_engine = dbengine('dawndb')

In [ ]:
################################### Average Portfolio Sales Turnover - as of last monthend from today
#Actually: Rolling months sum of (total bond sales proceeds + paydown)/monthly NAV
fund='BRINKER'
sql_string = "SELECT * FROM bonds WHERE buysell IS False and fund = %s order by trade_date desc"
df = pd.read_sql_query(sql_string, dawn_engine,
                       parse_dates={'lastupdate':{'utc':True}, 'trade_date': {}, 'settle_date':{}},
                       params=[fund,],
                       index_col = 'trade_date')
df = df.groupby(pd.Grouper(freq='M')).sum()

brinker_nav = pd.read_csv(
        "/home/serenitas/edwin/Python/brinker_nav.csv",
        parse_dates=["date"],
        index_col=["date"])

start_date = datetime.date(2019,3,18)
end_date = datetime.date.today()
cf = pd.read_sql_query("SELECT * FROM cashflow_history where date > %s and date <= %s", dawn_engine,
                       params=[start_date, end_date],
                       parse_dates=['date'],
                       index_col=['date']).sort_index()
sql_string = "SELECT description, identifier, notional, price, factor FROM risk_positions(%s, %s, 'BRINKER')"
pos = {}
for d in cf.index.unique():
    for ac in ['Subprime', 'CRT']:
        pos[d, ac] = pd.read_sql_query(sql_string, dawn_engine, params=[d.date(), ac])
pos = pd.concat(pos, names=['date', 'asset_class'])
pos = pos.reset_index(level=[1,2])

cf_1 = pd.merge_asof(cf, pos.sort_index(), left_index=True, right_index=True, by='identifier')
cf_1 = cf_1.dropna(subset=['notional'])
cf_1 = cf_1[(cf_1.principal_bal != 0) & (cf_1.principal != 0)]
cf_1['paydown'] = cf_1.apply(lambda df: df.notional * df.factor/df.principal_bal * df.principal, axis=1)
paydowns = cf_1.paydown.groupby(pd.Grouper(freq='M')).sum()
turnover = pd.concat([paydowns, df.principal_payment, df.accrued_payment], axis=1).fillna(0)
brinker_nav = brinker_nav.groupby(pd.Grouper(freq='M')).last()
turnover = (turnover.sum(axis=1)/brinker_nav.nav).rolling(min(13, len(turnover))-1).sum()